In [1]:
import credentials_latest as credentials
import settings_bjp as settings
import re
import tweepy
import mysql.connector
import pandas as pd
import numpy
import torch
import time
from transformers import XLMRobertaTokenizer, XLMRobertaConfig, XLMRobertaForSequenceClassification

In [2]:
tokenizer = XLMRobertaTokenizer.from_pretrained('xlm-roberta-base', do_lower_case=True)
model_state_dict = torch.load('xlmr_model2.bin', map_location=torch.device('cpu'))
config = XLMRobertaConfig.from_pretrained('xlm-roberta-base', num_labels=3, output_hidden_states=False, output_attentions = False)
model = XLMRobertaForSequenceClassification.from_pretrained('xlm-roberta-base', config = config, state_dict = model_state_dict)

Some weights of XLMRobertaForSequenceClassification were not initialized from the model checkpoint at xlm-roberta-base and are newly initialized: ['roberta.pooler.dense.weight', 'roberta.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [3]:
def textClean(text):
    if text:
        partial_cleaned_text_1 = re.sub(r'http\S+', '', text.lower())
        partial_cleaned_text_2 = re.sub(r'[^A-Za-z0-9 ]+', "", partial_cleaned_text_1)
        cleaned_text = re.sub(r"^\s+|\s+$", "", partial_cleaned_text_2)
        return cleaned_text
    else:
        return None

In [4]:
class MyStreamListener(tweepy.StreamListener):
    def on_status(self, status):
        try:
            if status.retweeted == False and status.text.startswith('RT @') == False:
                id_str = status.id_str
                created_at = status.created_at
                text = textClean(status.text)
                user_location = textClean(status.user.location)
                encoded_text = tokenizer.encode_plus(
                    text, add_special_tokens = True, 
                    max_length = 128, 
                    padding = True, 
                    return_attention_mask = True, 
                    return_token_type_ids = True, 
                    return_tensors = 'pt'
                )
                outputs = model(**encoded_text)
                output = outputs[0].detach().numpy()
                sentiment = int(numpy.argmax(output))
                print(text)
                print("-----------------")

                if mydb.is_connected():
                    mycursor = mydb.cursor()
                    sql = "INSERT INTO {} (id_str, created_at, text, sentiment, user_location) VALUES (%s, %s, %s, %s, %s)".format(settings.TABLE_NAME)
                    val = (id_str, created_at, text, sentiment, user_location)
                    mycursor.execute(sql, val)
                    mydb.commit()
                    mycursor.close()
                    
                return True
        except (AttributeError, Exception) as e:
            print(e)
    
    def on_error(self, status_code):
        print(status)

In [5]:
mydb = mysql.connector.connect(
    host="localhost",
    user="root",
    passwd="rootpassword",
    database="TwitterDB",
    charset = 'utf8'
)

if mydb.is_connected():
    '''
    Check if this table exits. If not, then create a new one.
    '''
    mycursor = mydb.cursor()
    mycursor.execute("""
        SELECT COUNT(*)
        FROM information_schema.tables
        WHERE table_name = '{0}'
        """.format(settings.TABLE_NAME))
    if mycursor.fetchone()[0] != 1:
        mycursor.execute("CREATE TABLE {} ({})".format(settings.TABLE_NAME, settings.TABLE_ATTRIBUTES))
        mydb.commit()
    mycursor.close()

In [6]:
auth  = tweepy.OAuthHandler(credentials.API_KEY, credentials.API_SECRET_KEY)
auth.set_access_token(credentials.ACCESS_TOKEN, credentials.ACCESS_TOKEN_SECRET)
api = tweepy.API(auth)

In [ ]:
while True:
    try:
        print('------------------------------------------')
        myStreamListener = MyStreamListener()
        myStream = tweepy.Stream(auth = api.auth, listener = myStreamListener)
        myStream.filter(languages=["en"], track = settings.TRACK_WORDS)
    
    except Exception as e:
        print(e)
        print('Disconnected...')
        time.sleep(5)
        continue

------------------------------------------
monikasinghsays congress ke up ke bhut bde leader jitin prasad hue bjp mein shamil vipkchh dloo mein mcheee khalbli
-----------------
its frustration of nationalist forces in congress who are by blood and heridity nationalist but were suppressed by
-----------------
narendramodi now bjp become congress yukt  do whatever in bit to win up  you will not succeed becuase bjp never
-----------------
nordicgujju technically bjp cant be leaning towards any group as long as they are not anti indigenous  thats g
-----------------
a large group of alcoholic people will go against yogi means another nail on bjps coffin govt is trying to make
-----------------
if sachinpilot is made the main face of congress its gonna be little tough for bjp what do you think
-----------------
indiatoday preetichoudhry congress is still not winning elections so what congress has to lose from himbut th
-----------------
srinivasburra9 mayuri63740250 bjp4telangana sagar4bjp 

desiboho most indians  in science in the west i know are anti bjp  like venkat ramakrishnan
-----------------
aitcofficial bjp4india mamataofficial sure but where that money would go will be decided by namo and bjp hope
-----------------
this is for the sikhs keshadhari hindus who are still under the spell of bjprss propaganda i know even they wil
-----------------
thelibrawomen bharat will never be congress muktinfact bjp is getting congressified
-----------------
jitinprasada when r u pulling sachin pilot to bjp  jpnadda ctravi sachinpilot annamalai
-----------------
drogosniper absolutely sirjust read a good observationthat y only ex congress workers r switching high in
-----------------
sujataganguly13 he wins but for bjp exclusively
-----------------
congratulations modi ji brilliant century in karnatakawell played team bjppetrolpricehike
-----------------
timesnow jdhankhar1 thenewshour bengal is not on fire it is fire the governors ass is on fire after bjp losing
---------------

congress mukt barath is becoming a reality raga is bjps sleeper cell
-----------------
prabhutommy kodungolan737 but thats long way rss bjp and brahmins will make sure common people dont get that clarity
-----------------
when the friends leave
-----------------
anjali21s opindiacom dont forget bjp win more than 70 seats party which is has zero seats to more than 70 that
-----------------
ten bjp mlas in odisha urged the state government to amend the guidelines on spending of mla lad fund
-----------------
dabbu72107101 pal79862374 turehnnde ndtv hello empty skull you are still defending the idiots who said they wi
-----------------
sardesairajdeep jitinprasada its time for rahul gandhi to join bjp
-----------------
congress is not felt this way how this apna wala patalkars describing about jitin prasads worth for political p
-----------------
bjp party is cutting peoples pockets sometimes in the name of petrol sometimes in the name of diesel with the s
-----------------
drsangrampatil

zeeshan01dec rjfahad this fellow today joined bjp congrss is the team b of bjp
-----------------
thats very true
-----------------
after jitin prasad  rld leader jayant chaudhary may join bjp  bjp may give him rajya sabha mp seat  this is happ
-----------------
will in advance welcome
-----------------
ambkcsingh sir ji out of 4036 assembly seats in the country bjp has 1440 members congress has 760 membe
-----------------
abhishbanerj will mukul roy leave bjp
-----------------
abpnews rubikaliyaquat public ne rejected ker diya usi ko bjp 2022 me represent karegi
-----------------
absolutely righteven in his native shahjahanpur distupcongress without consulting himappointed a hostile pers
-----------------
hatefreeworldx brumbyoz as a party incindia is lacking ideologythey are sharing power with ss the party indic
-----------------
support these guys  these guys literally doing a thing which no rw bjp or rss leader has ever done
-----------------
srivatsayb arre bhai a person with a lit

bjp  would do well to trust its loyal cadres instead of roping in turncoats to improve its electoral prospects do you agree
-----------------
todays cartoon congressmen inbjp
-----------------
ranapaull sudhanidhib they never votes bjp  dont live in confusion
-----------------
assam bengal elections prove they are not losing any seats even in bengal they have 40 votes w 77 seats they
-----------------
ideology of loot and sicularism
-----------------
negisatpal1975 simigarewal good you didnt say he made lucknow the capital of india wonder is that even that wi
-----------------
jituladh timesofindia so that she can
-----------------
as soon as jitin prasad joins bjp hes been labeled as brahmin joining uppercaste hindutva party before that no
-----------------
ranapaull sudhanidhib be clear mullas never votes bjp
-----------------
myogiadityanath rahul gandhi joins bjprahulgandhijoinsbjprahulgandhijoinsbjp
-----------------
srivatsayb terencefdes arpitsriv12 why guys from congress or any

...

terabaaphu ye kisi low position wale ne chalu kiya he me khud bjp supporter hu and bjp khud vote gawa denge
-----------------
narendramodi inckarnataka siddaramaiah rahulgandhi mahuamoitra iyckarnataka srivatsayb sonusood
-----------------
amitshah dchautala buying selling shuru after the bengal debaclesee the doom of modi shah and all of you in the bjp
-----------------
congress it cell only trending and twitting this type of hashtag this is shown  which is the best government b
-----------------
shubhshaurya1 supriyashrinate talk about your congress party  bjp will manage your muslim mascot imran massod is flirting with akhilesh
-----------------
rahulgandhi bjp should learn from congress the more professional way congress is the pioneer in looting indiacongressmuktbharat
-----------------
stalwarts of oppo parties cant strategize to tak on bjp in 2024 ge  sad there are no mards in whole opposition
-----------------
akhileshpdsingh babanjhaind bjp wale congressi
-----------------
sha

abdullah0mar i think he has done a fabulous job for bjp by making opposition party and wiping out congress and cp
-----------------
pressers rescheduled tmc chief mamata banerjee to hold media conference at 430 pm amp westbengal bjp leaders to
-----------------
breaking tmc chief mamatabanerjee amp bjp national vice president mukulroy both en route tmcbhawan abhishek ba
-----------------
as mukulroy joins back tmc here is an important article 2 days back by onlineghosh in thewirein while mo
-----------------
after the assembly election results were announced on may 2 in fewer than 30 days the tmc captured twogram panch
-----------------
ndtv rsprasad i dont understand the oppose here in pandemic where we need to maintain social distance this is a
-----------------
myogiadityanath narendramodi our bjp yogi govt no expansion in  cabinet  no use of induction of jatinji already
-----------------
root out the regional parties as most of these parties are spreading anarchy castism facism com

according to nfsp govt portal both state govt amp central govt has role in pds schemebut centre govt has gone so l
-----------------
sanket ajitanjum when are you officially joining bjp
-----------------
sides of the same coin  bunch of jackasses  small world  no shame
-----------------
whether its bjp or congress the attitude remains the same aadiwasis have no voice and continue to suffer 3 w
-----------------
nagendr01514258 will always vote for bjp as it is best then all other worthless parties
-----------------
those who are the wealth of bjp is continuing with the saffron camp bjp chief dilip ghosh fpjindia
-----------------
exsecular when you have coward amp nonperforming narendramodi amp amitshah as chief patrons of bjp who dont care
-----------------
strike while the iron is hot trinamools strategy to stop bjp inbengal
-----------------
roiled by mass adivasi protests congress adopts bjp methods in chhattisgarh rahulgandhi incindia
-----------------
they have demonised sanghis 

bjp national secretarys lobby charge against his own he too had joined from the tmc
-----------------
mukul roy tmc to bjp
-----------------
gouravaitc who is commiting crimes here dont think its bjp
-----------------
bjp leader k surendran is a patriot involved in a money laundering case aisha sultana is a traitor who fought for
-----------------
bloody ghost has taken ober bloody waste bengal is this tagores bibekanandas west bengal or a satan waste benga
-----------------
protest against pmoindia bjp for petrol diesel gas price  hike
-----------------
if you are aisha or asma or whatever muslim name they must be booked if they speak up for truth and thats the unwri
-----------------
this is prejudice speaking not reasoning almost every one who votes for bjp is a self loathing whining piece of du
-----------------
nothing remotely surprising about this you dont need a survey to know that
-----------------
one step ahead no one support 315 mlasthen where is the question of total bjp g

dhfwka khatachara bjp government thooo thoooo
-----------------
khanumarfa you seem to think bjp and its supporters are the only ones living in india
-----------------
200 agree
-----------------
funny how i only get bjp related news in my notifications section is this what they held twitter on chokehold fo
-----------------
if the current state of country doesnt bother you then it is pretty sad
-----------------
will sharmilas new party beleaguered bjp groundgain in trs bastion
-----------------
shiv sena takes dig at bjp says hilarious to see party seeking help of jitin prasada to woobrahmins
-----------------
shobhamookerje1 if he joins bjp he will be a small fish in big pond if he remains he will be big fish in small co
-----------------
amitmalviya nitingadkari myogiadityanath please work out the strategy to protect bjp4bengal otherwise it will
-----------------
national vice president joing tmc is the biggest embarrassment then anything  bjp should hang themselves of shame
------